# Shear mode device
**Absorption frequency shift simulations**

In [1]:
import numpy as np
import pandas as pd

from nems_fingerprint import *
from comsol_mesh import *

In [2]:
# Plotting
import bokeh
import bokeh.palettes as palettes
from bokeh.io import show, output_notebook
from bokeh.plotting import figure
from bokeh.models import ColumnDataSource
from bokeh.layouts import Column, gridplot

palette = palettes.Category10[10]
output_notebook()


# Plot defaults
line_settings = dict(
    line_width=2,
    muted_alpha=0.1
)

fig_settings = dict(
    width=500,
    height=350
)

tool_settings = dict(
    toolbar_location=None,
    tools=[]
)

# Convenience functions
def pairs(it):
    a = iter(it)
    b = iter(it)
    b.__next__()
    return list(zip(a, b))

Loading BokehJS ...

## Device eigenmodes

### Import

In [28]:
# Load in device dimensionless frequencies
E_silicon = 169.0   # Young's modulus [GPa]
ρ_silicon = 2329.0  # density [Kg m^-3]
L_device = 1.0      # Characteristic length [μm]

f0 = np.sqrt(10 ** 3 * E_silicon / ρ_silicon)  # characteristic frequency [GHz]

device_dim_freqs = np.array(pd.read_csv(
    'data/shear_device_frequencies.csv',
    skiprows=5,
    header=None,
    usecols=[0,],
    names=['freqs',]
).freqs)

device_freqs = device_dim_freqs * f0  # device frequencies [GHz]

# Load device geometry
comsol_objs = COMSOLObjects.from_file('data/shear_device.mphtxt')
cobj = comsol_objs[0]
mesh = Mesh.from_comsol_obj(cobj)

# Load device eigenmodes
cemodes = COMSOLEigenmodes.from_file('data/shear_device_eigenmodes.csv')
modes_field = Field.from_comsol_field(mesh, cemodes)

# Load top surface
surfaces = surfaces_from_comsol_obj(mesh, cobj)
top_surface = surfaces[-1]
top_surface

Surface(
    mesh=Mesh(n_points=2823, n_tetrahedra=13851),
    n_triangles=582
)

### Plot geometry

In [19]:
labels = ('x [μm]', 'y [μm]', 'z [μm]')
titles = ('Side-view', 'Top-view')

ps = []

for (title, (i1, i2)) in zip(titles, ((0, 1), (2, 1))):
    p = figure(
        title=title,
        x_axis_label=labels[i1],
        y_axis_label=labels[i2],
        margin=20,
        match_aspect=True,
        height=400,
        width=400
    )
    p.scatter(mesh.points[:, i1], mesh.points[:, i2])
    
    ps.append(p)
    
for p in ps:
    p.xaxis.axis_label_text_font_size = "14pt"
    p.yaxis.axis_label_text_font_size = "14pt"
    p.title.text_font_size = '14pt'


gs = gridplot(ps, ncols=2)
show(gs)

### Plot eigenmodes

In [16]:
# Evaluate modes over uniform grid

# Define grid
Ny = 200
Nz = 150

x0 = 0.3
y1, y2 = 0.2, 1.2
z1, z2 = -0.6, 0.6

ys = np.linspace(y1, y2, Ny)
zs = np.linspace(z1, z2, Nz)

grid_pts = np.empty((Ny, Nz, 3))
grid_values = np.empty((Ny, Nz) + modes_field.field_shape)

for i, y in enumerate(ys):
    for j, z in enumerate(zs):
        point =  [x0, y, z]
        grid_pts[i, j, :] = point
        grid_values[i, j, :, :] = modes_field.eval_surface_point(top_surface, point)


grid_norms = np.linalg.norm(grid_values, axis=-1)

In [20]:
N_modes_plotted = 4

ps = []
for i in range(N_modes_plotted):
    for j, label in enumerate('XYZ'):
        p = figure(
            title=f'Mode {i + 1} - {label}-deflection',
            x_axis_label='y [μm]',
            y_axis_label='z [μm]',
            margin=15
        )

        p.image(
            image=[grid_values[:, :, i, j].T],
            x=y1, y=z1, dw=y2 - y1, dh=z2 - z1,
            palette="Sunset11",
            level="image"
        )

        p.x_range.range_padding = 0
        p.y_range.range_padding = 0
        
        if len(ps) > 0:
            p.x_range = ps[0].x_range
            p.y_range = ps[0].y_range
            
        ps.append(p)
    
for p in ps:
    p.xaxis.axis_label_text_font_size = "12pt"
    p.yaxis.axis_label_text_font_size = "12pt"
    p.title.text_font_size = '12pt'
        
gs = gridplot(ps, ncols=3, width=350, height=350)
show(gs)

In [30]:
ps = []
for i in range(modes_field.field_shape[0]):
    p = figure(
        title=f'Mode {i + 1}:  {device_freqs[i]:5.3f} GHz',
        x_axis_label='y [μm]',
        y_axis_label='z [μm]'
    )

    p.image(
        image=[grid_norms[:, :, i].T],
        x=y1, y=z1, dw=y2 - y1, dh=z2 - z1,
        palette="Sunset11",
        level="image"
    )

    p.x_range.range_padding = 0
    p.y_range.range_padding = 0

    if len(ps) > 0:
        p.x_range = ps[0].x_range
        p.y_range = ps[0].y_range

    ps.append(p)

for p in ps:
    p.xaxis.axis_label_text_font_size = "12pt"
    p.yaxis.axis_label_text_font_size = "12pt"
    p.title.text_font_size = '12pt'
        
gs = gridplot(ps, ncols=3, width=350, height=350)

show(gs)